In [1]:
import h5py
import pylab as pl
import numpy as np
import matplotlib.colors as mpc
import networkx
import ipyvolume as ipv
import progressbar

In [2]:
pl.rc('font', size = 20)
pl.rc('legend', fontsize = 20)

In [3]:
def split_unique_id(unique_id):
    """Splits the ids assign to the subhalos by the merger tree code by snap number and subfind number """
    subfind_number = int(unique_id % 1e6)
    snap_number = int((unique_id - subfind_number) / 1e6)
    
    return snap_number, subfind_number

def get_main_branch_unique_ids(subtree, node):
    """Gets the unique ids of the subhalos belonging to the main branch of the selected subhalo (node)"""
    mpb = [node, ]
    i = 0
    while True:
        succesors = list(subtree.successors(node))
        if len(succesors) == 0:
            break
        node = succesors[0] # select only the first succesor (main branch)
        mpb.append(node)
        
    return mpb

def get_main_branch_and_progNumb(subtree, node):
    """Gets the unique ids of the subhalos belonging to the main branch of the selected subhalo (node)"""
    mpb = [node, ]
    numb = [[node], ]
    i = 0
    while True:
        successors = list(subtree.successors(node))
        if len(successors) == 0:
            break
        node = successors[0] # select only the first succesor (main branch)
        mpb.append(node)
        numb.append(successors)
        
    return mpb, numb


def set_view(figure, framenr, fraction):
    ipv.view(fraction*360, 0.)
    
def set_angles(fig, i, fraction):
    fig.angley = fraction*np.pi*2

# a bunch of constants
UnitMass_in_g = 1.989e+43
UnitTime_in_s = 3.08568e+16
UnitVelocity_in_cm_per_s = 100000
UnitDensity_in_cgs = 6.7699e-22
UnitEnergy_in_cgs = 1.989e+53
GAMMA_MINUS1 = 2./3.
PROTONMASS = 1.6726e-24
BOLTZMANN = 1.3806e-16    

def tempFromMass(Mass, Abund, IE, ne1):
    XH = Abund[:,6]/Mass
    yHelium = (1. - XH)/(4.*XH)
    mu = (1 + 4.* yHelium)/ (1.+ yHelium + ne1 )
    temp = GAMMA_MINUS1 * IE * mu * 1.6726 / 1.3806 * 1.e-8 # / BOLTZMANN  * PROTONMASS
    temp = temp * 1e10 #   UnitEnergy_in_cgs / UnitMass_in_g;
    return temp

In [4]:
sim = h5py.File('/data/cielo/simulations/LG1/LG1.hdf5', 'r')
trees = networkx.read_multiline_adjlist('/data/cielo/simulations/LG1/LG1_tree.dat')

In [5]:
def plotPhaseSpace(fofID, centralID):
    
    uniqueID = int(128*1e6+fofID)
    stree = networkx.dfs_tree(trees, str(uniqueID))
    mtree, numbs = get_main_branch_and_progNumb(stree, str(uniqueID))
    
    uniqueC = int(128*1e6+centralID)
    streeC = networkx.dfs_tree(trees, str(uniqueC))
    mtreeC = get_main_branch_unique_ids(streeC, str(uniqueC))
    
    # find all the particleIDs that once belong to the subgroup
#     Idlist, vallist, valcen = [], [], []
    #Idlist, vallist = [], []
    Idlist = []
    
    for mm, mmC in zip(mtree[1:], mtreeC[1:]): # ignore the first one
        snap, idd = split_unique_id(int(mm))
        snapC, iddC = split_unique_id(int(mmC))
        tempOff = sim['SnapNumber_{}/SubGroups/PartType0/Offsets'.format(snap)][idd].astype('int')
        pgal = sim['SnapNumber_{}/SubGroups/SubGroupPos'.format(snap)][idd]
        if snapC==snap:
            pcen = sim['SnapNumber_{}/SubGroups/SubGroupPos'.format(snapC)][iddC]
        if tempOff[0]>= 0 and tempOff[1]>=0:
            tempIds = sim['SnapNumber_{}/PartType0/ParticleIDs'.format(snap)][tempOff[0]:tempOff[1]]
            Idlist.extend(list(tempIds))
            # calcule the value for color coding the graph
            #val = sim['SnapNumber_{}/Header/Redshift'.format(snap)][()]
            #IE = sim['SnapNumber_{}/PartType0/InternalEnergy'.format(snap)][tempOff[0]:tempOff[1]]
            #Mass = sim['SnapNumber_{}/PartType0/Masses'.format(snap)][tempOff[0]:tempOff[1]]
            #Abund = sim['SnapNumber_{}/PartType0/Abundances'.format(snap)][tempOff[0]:tempOff[1]]
            #ne1 = sim['SnapNumber_{}/PartType0/ElectronAbundance'.format(snap)][tempOff[0]:tempOff[1]]
            #val = tempFromMass(Mass, Abund, IE, ne1)
            #val = sim['SnapNumber_{}/PartType0/BindingEnergy'.format(snap)][tempOff[0]:tempOff[1]]
            #return None
            # if val is one for each particles just append, otherwise do the next
            #vallist.extend([val]*tempIds.size)
            # or
            #vallist.extend(list(val))

    #Idlist, vallist = np.array(Idlist), np.array(vallist)
    Idlist = np.array(Idlist)
    Idlist, Idunique = np.unique(Idlist, return_index=True) # remove duplicates
    #vallist = vallist[Idunique]
    
    # the total list of particles that once belong to a give subgroup, lest see where are today.
    TdayOff = sim['SnapNumber_128/SubGroups/PartType0/Offsets'][fofID].astype('int')
    
    TdayCoord = sim['SnapNumber_128/PartType0/Coordinates'][TdayOff[0]:TdayOff[1]]

    TdayTotalIDs = sim['SnapNumber_128/PartType0/ParticleIDs'][()]
    
    IndexToday = np.in1d(TdayTotalIDs, Idlist)
    IndexToday_ = np.where(IndexToday)[0]
    
    #remove the ones that are not part of the group today.
    TdayIDs = sim['SnapNumber_128/PartType0/ParticleIDs'][TdayOff[0]:TdayOff[1]]
    
    IndexNot = np.in1d(Idlist, TdayIDs)
    IdNot = Idlist[np.where(IndexNot==False)[0]]

    IndexT = np.in1d(TdayTotalIDs, IdNot)
    IndexT_ = np.where(IndexT)[0]
    
    
    #print(IndexT_[0], IndexT_[int(IndexT_.size/2)], IndexT_[-1])
    
    LostCoord = sim['SnapNumber_128/PartType0/Coordinates'][IndexT_]
    
    
#     # ... and the redshift
#     SurvIds_ = TdayTotalIDs[IndexT_]
#     iidex = np.in1d(Idlist, SurvIds_)
#     iidex_ = np.where(iidex)[0]
#     vallist_, Idlist_ = vallist[iidex_], Idlist[iidex_]

#     is1 = np.argsort(SurvIds_) # the target
#     is2 = np.argsort(Idlist_)

#     valorder = np.zeros(IndexT_.size)
#     valorder[is1] = vallist_[is2]
    
    #now lets cut at  a certain distance
    distance = 600 # distance in ckpc

    posGal = sim['SnapNumber_128/SubGroups/SubGroupPos'][fofID]
    posCen = sim['SnapNumber_128/SubGroups/SubGroupPos'][centralID]

    dx, dy, dz = LostCoord[:,0]-posGal[0], LostCoord[:,1]-posGal[1], LostCoord[:,2]-posGal[2]
    distToC = np.sqrt(dx**2+dy**2+dz**2)

    icut = np.where(distToC<distance)[0]
    IndexT_near = IndexT_[icut]
    
    #valorder_near = valorder[icut]
    #IndexT_near = IndexT_
    #valorder_near = valorder
    
    NearCoord = sim['SnapNumber_128/PartType0/Coordinates'][IndexT_near]
    NearVel = sim['SnapNumber_128/PartType0/Velocities'][IndexT_near]
    
    #and the current status
#     Status = np.zeros(IndexT_near.size)
    
#     Thegroup = sim['SnapNumber_128/SubGroups/GroupNumber'][fofID]
#     gro = sim['SnapNumber_128/SubGroups/GroupNumber'][centralID]
    
#     PartGroup = sim['SnapNumber_128/PartType0/GroupNumber'][IndexT_near]
#     PartSubGroup = sim['SnapNumber_128/PartType0/SubGroupNumber'][IndexT_near]
    
#     free = np.where((PartGroup == -1) & (PartSubGroup ==-1))
#     ICM = np.where((PartGroup == Thegroup) & (PartSubGroup ==-1))
#     centralGal = np.where(PartSubGroup == 0)
#     otherGal = np.where((PartGroup == Thegroup) & (PartSubGroup > 0))
#     otherGroup = np.where((PartGroup != Thegroup) & (PartGroup != -1))
    
#     Status[free] = 0
#     Status[ICM] = 1
#     Status[centralGal] = 2
#     Status[otherGal] = 3
#     Status[otherGroup] = 4
    
    
    # here i make the cut.
    return NearCoord, NearVel#, Status

In [6]:
#  4338, 4341 (4337), 4470 y 4474 (4469)
# NearCoord, NearVel = plotPhaseSpace(4341,4337)

In [7]:
# print(NearCoord.shape)

# cen = sim['SnapNumber_128/SubGroups/SubGroupPos'][4341]
# cenvel =  sim['SnapNumber_128/SubGroups/SubGroupVel'][4341]

# rad = sim['SnapNumber_128/SubGroups/OpticalRadius'][4341]
# veldisp = sim['SnapNumber_128/SubGroups/SubGroupVelDisp'][4341]


# x, y, z = NearCoord[:,0] - cen[0], NearCoord[:,1] - cen[1], NearCoord[:,2] - cen[2]
# xv, yv, zv = NearVel[:,0]-cenvel[0], NearVel[:,1]-cenvel[1], NearVel[:,2]-cenvel[2]

# r = np.sqrt(x**2+y**2+z**2)
# v = np.sqrt(xv**2+yv**2+zv**2)

# rr = r/rad
# vv = v/veldisp

# papels = np.array([-0.5, 0.5, 1.5, 2.5, 3.5, 4.5])

# fig = ipv.figure(width=750, height=750)

# scatter = ipv.scatter(x, y, z, marker='sphere', size=.25, color='red')

# ipv.show()

In [8]:
# ok, make a list of all satellites of 4337
groups = sim['SnapNumber_128/SubGroups/GroupNumber'][()]
group = groups[4337]

sat = np.where(groups==group)[0][1:]
print(sat)

[4338 4339 4340 4341 4342 4343 4344 4345 4346 4347 4348 4349 4350 4351
 4352 4353 4354 4355 4356 4357 4358 4359 4360 4361 4362 4363 4364 4365
 4366 4367 4368 4369 4370 4371 4372 4373 4374 4375 4376 4377 4378 4379
 4380 4381 4382 4383 4384 4385 4386 4387 4388 4389 4390 4391 4392 4393
 4394 4395 4396 4397 4398 4399 4400 4401 4402 4403 4404 4405 4406 4407
 4408 4409 4410 4411 4412 4413 4414 4415 4416 4417 4418 4419 4420 4421
 4422 4423 4424 4425 4426 4427 4428 4429 4430 4431 4432 4433 4434 4435
 4436 4437 4438 4439 4440 4441 4442 4443 4444 4445 4446 4447 4448 4449
 4450 4451 4452 4453 4454 4455 4456 4457 4458 4459 4460 4461 4462 4463
 4464 4465 4466 4467 4468]


In [9]:
# and of all satellites of 4469
group2 = groups[4469]

sat2 = np.where(groups==group2)[0][1:]
print(sat2)

[4470 4471 4472 4473 4474 4475 4476 4477 4478 4479 4480 4481 4482 4483
 4484 4485 4486 4487 4488 4489 4490 4491 4492 4493 4494 4495 4496 4497
 4498 4499 4500 4501 4502 4503 4504 4505 4506 4507 4508 4509 4510 4511
 4512 4513 4514 4515 4516 4517 4518 4519 4520 4521 4522 4523 4524 4525
 4526 4527 4528 4529 4530 4531 4532 4533 4534 4535 4536 4537 4538 4539
 4540 4541 4542 4543 4544 4545 4546 4547 4548 4549 4550 4551 4552 4553
 4554 4555 4556 4557 4558 4559 4560 4561 4562 4563 4564 4565 4566 4567
 4568 4569 4570 4571 4572 4573 4574 4575 4576 4577 4578 4579 4580 4581
 4582 4583 4584 4585 4586 4587 4588 4589 4590 4591 4592 4593 4594 4595
 4596 4597 4598 4599 4600 4601 4602 4603 4604 4605 4606 4607 4608 4609
 4610 4611 4612 4613 4614 4615 4616 4617 4618 4619 4620 4621 4622 4623
 4624 4625 4626 4627]


In [10]:
def ploty(cen, sa):
    gro = groups[cen]
    cenG = sim['SnapNumber_128/Groups/GroupCM'][gro]
    cenBCG = sim['SnapNumber_128/SubGroups/SubGroupPos'][cen]
    cenGal = sim['SnapNumber_128/SubGroups/SubGroupPos'][sa]
    
    print(cenBCG[0]-cenG[0], cenBCG[1]-cenG[1], cenBCG[2]-cenG[2])
    
    fig = ipv.figure(width=750, height=750)
    
    snap = ipv.scatter(np.array([cenG[0]-cenG[0]]), np.array([cenG[1]-cenG[1]]), np.array([cenG[2]-cenG[2]]), color='black', marker='sphere')
    snap2 = ipv.scatter(np.array([cenBCG[0]-cenG[0]]), np.array([cenBCG[1]-cenG[1]]), np.array([cenBCG[2]-cenG[2]]), color='red', marker='sphere')
    snap3 = ipv.scatter(cenGal[:,0]-cenG[0], cenGal[:,1]-cenG[1], cenGal[:,2]-cenG[2], color='green', marker='sphere')
    
    ipv.show()

In [11]:
# ploty(4337, sat)

In [12]:
# ploty(4469, sat2)

In [13]:
X, Y, Z = [], [], []
VX, VY, VZ = [], [], []

pbar = progressbar.ProgressBar(max_value=sat.size)

for i, ss in enumerate(sat):
    NearCoord, NearVel = plotPhaseSpace(ss,4337)
    X.extend(list(NearCoord[:,0]))
    Y.extend(list(NearCoord[:,1]))
    Z.extend(list(NearCoord[:,2]))
    
    VX.extend(list(NearVel[:,0]))
    VY.extend(list(NearVel[:,1]))
    VZ.extend(list(NearVel[:,2]))

    pbar.update(i)
    
X, Y, Z  = np.array(X), np.array(Y), np.array(Z)
VX,VY, VZ = np.array(VX), np.array(VY), np.array(VZ)

 99% (130 of 131) |##################### | Elapsed Time: 0:04:17 ETA:   0:00:00

In [14]:
cenT = sim['SnapNumber_128/SubGroups/SubGroupPos'][4337]
velT = sim['SnapNumber_128/SubGroups/SubGroupVel'][4337]

Xn, Yn, Zn = X-cenT[0], Y-cenT[1], Z-cenT[2]
VXn ,VYn, VZn = VX-velT[0] ,VY-velT[1] , VZ-velT[2]

In [15]:
# fig = ipv.figure(width=750, height=750)

# scatter = ipv.scatter(Xn, Yn, Zn, marker='sphere', size=.05, color='red')

# ipv.show()

In [16]:
G = 4.3009*1e-6 # in kpc (km/s)^2 M_sun^-1
M200 = sim['SnapNumber_128/Groups/Group_M_Crit200'][group]
R200 = sim['SnapNumber_128/Groups/Group_R_Crit200'][group]

M200 = M200*1e10
vdisp = np.sqrt(G*M200/R200)
#vYang = 397.9 * (M200/1e14)**(0.3214)

In [17]:
XnR, YnR, ZnR = Xn/R200, Yn/R200, Zn/R200

# fig = ipv.figure(width=750, height=750)

# scatter = ipv.scatter(XnR, YnR, ZnR, marker='sphere', size=.05, color='red')

# ipv.show()

In [18]:
# and now the other group

In [19]:
X2, Y2, Z2 = [], [], []
VX2,VY2, VZ2 = [], [], []

pbar2 = progressbar.ProgressBar(max_value=sat2.size)

for i, ss in enumerate(sat2):
    NearCoord2, NearVel2 = plotPhaseSpace(ss,4469)
    X2.extend(list(NearCoord2[:,0]))
    Y2.extend(list(NearCoord2[:,1]))
    Z2.extend(list(NearCoord2[:,2]))
    
    VX2.extend(list(NearVel2[:,0]))
    VY2.extend(list(NearVel2[:,1]))
    VZ2.extend(list(NearVel2[:,2]))
    
    pbar2.update(i)
    
X2, Y2, Z2  = np.array(X2), np.array(Y2), np.array(Z2)
VX2, VY2, VZ2 = np.array(VX2), np.array(VY2), np.array(VZ2)

 99% (157 of 158) |##################### | Elapsed Time: 0:12:30 ETA:   0:00:00

In [20]:
group, group2

(4671, 4672)

In [21]:
cenT2 = sim['SnapNumber_128/SubGroups/SubGroupPos'][4469]
velT2 = sim['SnapNumber_128/SubGroups/SubGroupVel'][4469]

Xn2, Yn2, Zn2 = X2-cenT2[0], Y2-cenT2[1], Z2-cenT2[2]
VXn2 ,VYn2, VZn2 = VX2-velT2[0] ,VY2-velT2[1] , VZ2-velT2[2]

In [22]:
# fig = ipv.figure(width=750, height=750)

# scatter = ipv.scatter(Xn2, Yn2, Zn2, marker='sphere', size=.05, color='red')

# ipv.show()

In [23]:
G = 4.3009*1e-6 # in kpc (km/s)^2 M_sun^-1
M200_2 = sim['SnapNumber_128/Groups/Group_M_Crit200'][group2]
R200_2 = sim['SnapNumber_128/Groups/Group_R_Crit200'][group2]

M200_2 = M200_2*1e10
vdisp2 = np.sqrt(G*M200_2/R200_2)
#vYang = 397.9 * (M200/1e14)**(0.3214)

In [24]:
vdisp2

137.027039706534

In [25]:
XnR2, YnR2, ZnR2 = Xn2/R200_2, Yn2/R200_2, Zn2/R200_2

# fig = ipv.figure(width=750, height=750)

# scatter = ipv.scatter(XnR2, YnR2, ZnR2, marker='sphere', size=.05, color='red')

# ipv.show()

In [26]:
posGals = sim['SnapNumber_128/SubGroups/SubGroupPos'][sat]
posGals2 = sim['SnapNumber_128/SubGroups/SubGroupPos'][sat2]

In [27]:
off1 = sim['SnapNumber_128/SubGroups/PartType1/Offsets'][sat].astype('int')
off2 = sim['SnapNumber_128/SubGroups/PartType1/Offsets'][sat2].astype('int')

# Mass = []

# for o1, o2 in zip(off1[:,0], off1[:,1]):
#     masses = sim['SnapNumber_128/PartType0/Masses'][o1:o2]
#     Mass.append(np.sum(masses))
    
# Mass = np.array(Mass)

# Mass2 = []

# for o1, o2 in zip(off2[:,0], off2[:,1]):
#     masses = sim['SnapNumber_128/PartType0/Masses'][o1:o2]
#     Mass2.append(np.sum(masses))
    
# Mass2 = np.array(Mass2)

Mass = (off1[:,1]-off1[:,0])*0.00010843
Mass2 = (off2[:,1]-off2[:,0])*0.00010843

OffC = sim['SnapNumber_128/SubGroups/PartType1/Offsets'][4337]
OffC2 = sim['SnapNumber_128/SubGroups/PartType1/Offsets'][4469]

MassC = (OffC[1]-OffC[0])*0.00010843
MassC2 = (OffC2[1]-OffC2[0])*0.00010843

In [28]:
xGal, yGal, zGal = posGals[:,0] - cenT[0], posGals[:,1] - cenT[1], posGals[:,2] - cenT[2]
xGal2, yGal2, zGal2 = posGals2[:,0] - cenT2[0], posGals2[:,1] - cenT2[1], posGals2[:,2] - cenT2[2]

In [29]:
xGalR, yGalR, zGalR = xGal/R200, yGal/R200, zGal/R200
xGalR2, yGalR2, zGalR2 = xGal2/R200_2, yGal2/R200_2, zGal2/R200_2

In [30]:
fig = ipv.figure(width=750, height=750)

zero = np.zeros(1)

MassC = Mass.max()

scatter = ipv.scatter(XnR, YnR, ZnR, marker='sphere', size=.05, color='red')
scatterG = ipv.scatter(xGalR, yGalR, zGalR, marker='sphere', size=Mass*7, color='black')
scatterC = ipv.scatter(zero, zero, zero, marker='sphere', size=MassC*7, color='green')

ipv.show()

In [31]:
# def set_angles(fig, i, fraction):
#     fig.angley = fraction*np.pi*2
# ipv.movie('Pos_Group_4337.gif', set_angles, fps=20, frames=20*4, endpoint=False)

In [32]:
fig = ipv.figure(width=750, height=750)


MassC2 = Mass2.max()

scatter = ipv.scatter(XnR2, YnR2, ZnR2, marker='sphere', size=.05, color='red')
scatterG = ipv.scatter(xGalR2, yGalR2, zGalR2, marker='sphere', size=Mass2*0.5, color='black')
scatterC = ipv.scatter(zero, zero, zero, marker='sphere', size=MassC2*0.5, color='green')

ipv.show()